### Load libraries and external data

In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
import colored
from colored import stylize
from data import dataloader
import json
from neuralnet import nn
import numpy as np
import pandas as pd
import pixiedust_node #v≥0.2.5

Pixiedust database opened successfully


#### Load data from Firebase.
Requires [Firebase service account credentials](https://console.firebase.google.com/project/tingle-pilot-collected-data/settings/serviceaccounts/adminsdk) in JSON format saved in `./firebase-credentials`.

In [3]:
pilot_data, notes = dataloader.load_from_firebase(notes=True)
pilot_data = dataloader.break_out_blocks(pilot_data)

pixiedust_node 0.2.5 started. Cells starting '%%node' may contain Node.js code.
Data loaded from Firebase!


#### Load [Synaptic](http://caza.la/synaptic/)
If "Error: Cannot find module 'synaptic'", create and run these two cells:

1. ```
cd neuralnet
```

2. ```sh
!npm init -y
!npm install -s synaptic
```

In [5]:
%%node
var lstm = require('../../tingle-pilot-study/neuralnet/lstm.js');

---
### See all targets, number of available samples and iteration blocks

In [6]:
for target in list(pilot_data.target.unique()):
    ib =max(
        pilot_data.loc[
            pilot_data.target==target
        ].iteration_block.dropna()
    )
    print(": ".join([
        target,
        "{0} on-target samples in {1} iteration block{2}".format(
            str(len(pilot_data.loc[
                (pilot_data.target == target) &
                (pilot_data.ontarget)
            ])),
            "%.0f" % ib,
            "s" if ib != 1 else ""
        )
    ]))

none: 19 on-target samples in 2 iteration blocks
environment: 106 on-target samples in 4 iteration blocks
body: 101 on-target samples in 2 iteration blocks
cup: 33 on-target samples in 3 iteration blocks
food: 35 on-target samples in 4 iteration blocks
nails: 69 on-target samples in 3 iteration blocks
smoke: 92 on-target samples in 3 iteration blocks
eyebrow: 235 on-target samples in 5 iteration blocks
nose: 249 on-target samples in 4 iteration blocks
above-ear: 403 on-target samples in 5 iteration blocks
behind-ear: 220 on-target samples in 4 iteration blocks
opposite-cheek: 74 on-target samples in 6 iteration blocks
chin: 166 on-target samples in 1 iteration block
cheek: 686 on-target samples in 6 iteration blocks
forehead: 176 on-target samples in 1 iteration block
top-head: 160 on-target samples in 1 iteration block
back-head: 170 on-target samples in 1 iteration block
opposite-face: 381 on-target samples in 2 iteration blocks
paint-mouth: 81 on-target samples in 3 iteration blocks

---
### Extract training and testing data
Define targets of interest and corresponding offtargets

In [7]:
with open(
    'data/targets.json',
    'r'
) as fp:
    targets = json.load(
        fp
    )[0]

Set parameters for nn:

In [8]:
input_signals = [
    "distance",
    "thermopile1",
    "thermopile2",
    "thermopile3",
    "thermopile4"
]
iteration_blocks = list(range(1,7))
n_samples = 100

Get training inputs and outputs, inputs that should evaluate ~true and inputs that should evaluate ~false

In [9]:
data = {}
for target in targets:
    data[target] = {
        "train": nn.define_trainer_data(
            pilot_data,
            {
                "target": [target],
                "offtarget": targets[target]
            },
            input_signals,
            iteration_blocks,
            n_samples
        ),
        "test_true": nn.define_activation(
            pilot_data,
            [target],
            input_signals,
            iteration_blocks,
            exclude=n_samples
        ),
        "test_false": nn.define_activation(
            pilot_data,
            targets[target],
            input_signals,
            iteration_blocks,
            exclude=n_samples
        )
    }

Preview all inputs and training outputs

In [10]:
data

{'above-ear': {'test_false': [[0.0,
    0.8183760683760684,
    0.8719646799116998,
    0.8660812294182219,
    0.8551042810098793],
   [0.0,
    0.8162393162393163,
    0.8719646799116998,
    0.8507135016465424,
    0.8375411635565313],
   [0.0,
    0.811965811965812,
    0.870860927152318,
    0.8342480790340286,
    0.8342480790340286],
   [0.0,
    0.811965811965812,
    0.858719646799117,
    0.8441273326015369,
    0.8441273326015369],
   [0.0,
    0.8205128205128205,
    0.8664459161147904,
    0.8562019758507136,
    0.8616904500548848],
   [0.0,
    0.8322649572649574,
    0.8730684326710817,
    0.8496158068057081,
    0.8616904500548848],
   [0.6095617529880478,
    0.8376068376068377,
    0.9061810154525386,
    0.8957189901207464,
    0.8902305159165752],
   [0.0,
    0.8429487179487181,
    0.9061810154525386,
    0.9088913282107575,
    0.8792535675082327],
   [0.09163346613545817,
    0.8429487179487181,
    0.9094922737306844,
    0.9055982436882547,
    0.87925356750

**Note**: These data take some time to copy across environments. Give the notebook some time between running cells across Python and JavaScript.

---
### Train and test

In [20]:
%%node
var networks = {};
for (var target in data) {
  networks[target] = lstm.train_lstm([5,5,2,1], data[target]["train"], 0.06, 0.06, 300);
}

... ...
TRAINING 🏋 interations:300 🏋 minimum error:0.06 🏋 rate:0.06
iterations 5 error 0.08478576315323194 rate 0.06
iterations 10 error 0.08349242946256748 rate 0.06
iterations 15 error 0.08346064276405449 rate 0.06
iterations 20 error 0.08270957446604581 rate 0.06
iterations 25 error 0.08357077271153743 rate 0.06
iterations 30 error 0.08268763737942288 rate 0.06
iterations 35 error 0.08306363773327977 rate 0.06
iterations 40 error 0.08302673818173352 rate 0.06
iterations 45 error 0.08275051127915785 rate 0.06
iterations 50 error 0.08278172901398158 rate 0.06
iterations 55 error 0.08266971989306292 rate 0.06
iterations 60 error 0.0825980439724186 rate 0.06
iterations 65 error 0.08202087711773626 rate 0.06
iterations 70 error 0.08272034287986732 rate 0.06
iterations 75 error 0.08217092447552182 rate 0.06
iterations 80 error 0.08248082575026626 rate 0.06
iterations 85 error 0.08237522565854637 rate 0.06
iterations 90 error 0.08266126523576688 rate 0.06
iterations 95 error 0.082311285717

In [21]:
%%node
var test_outputs = {};
for (var target in data) {
    test_outputs[target] = {"true":[],"false":[]};
    for(var iteration=0; iteration < data[target]["test_true"].length; iteration++){
      test_outputs[target]["true"].push(networks[target].activate(data[target]["test_true"][iteration]));
      }
    for(var iteration=0; iteration < data[target]["test_false"].length; iteration++){
      test_outputs[target]["false"].push(networks[target].activate(data[target]["test_false"][iteration]));
    }
}

... ... ..... ..... ... ..... ..... ...


In [22]:
test_outputs

{'above-ear': {'false': [[0.0029916606907399138],
   [0.0016255334431060477],
   [0.0007776586484509699],
   [0.0010644275968331545],
   [0.0021391101231263937],
   [0.0023648697312731106],
   [6.54016589693381e-08],
   [0.02769668886981115],
   [0.004246310434871389],
   [0.03513280028238562],
   [0.024743227831577053],
   [0.026228283622997527],
   [0.000905764556624307],
   [0.03987295657223025],
   [0.030869474361291508],
   [0.028569232271750705],
   [0.008357098389207947],
   [0.03527937258837896],
   [0.035098940159217246],
   [0.024460727301956482],
   [0.0024945724614537325],
   [0.03437714085862752],
   [0.02460088484326464],
   [0.02792158736788146],
   [0.01983604805859791],
   [0.021679842643159145],
   [0.021013303565723278],
   [0.0278610818206145],
   [0.027131527415809445],
   [0.021993953710670484],
   [0.0248652203641667],
   [0.0025933569316516575],
   [0.03477000973986282],
   [0.025134432301547927],
   [0.02263026985682615],
   [0.008229169939705405],
   [0.028798

---
### See outputs

If the training is adequate x ≈ 0 ∀ x in the following:

In [33]:
f = {target: [
        outputs for outputs in test_outputs[target]['false']
] for target in targets}
f

{'above-ear': [[0.0029916606907399138],
  [0.0016255334431060477],
  [0.0007776586484509699],
  [0.0010644275968331545],
  [0.0021391101231263937],
  [0.0023648697312731106],
  [6.54016589693381e-08],
  [0.02769668886981115],
  [0.004246310434871389],
  [0.03513280028238562],
  [0.024743227831577053],
  [0.026228283622997527],
  [0.000905764556624307],
  [0.03987295657223025],
  [0.030869474361291508],
  [0.028569232271750705],
  [0.008357098389207947],
  [0.03527937258837896],
  [0.035098940159217246],
  [0.024460727301956482],
  [0.0024945724614537325],
  [0.03437714085862752],
  [0.02460088484326464],
  [0.02792158736788146],
  [0.01983604805859791],
  [0.021679842643159145],
  [0.021013303565723278],
  [0.0278610818206145],
  [0.027131527415809445],
  [0.021993953710670484],
  [0.0248652203641667],
  [0.0025933569316516575],
  [0.03477000973986282],
  [0.025134432301547927],
  [0.02263026985682615],
  [0.008229169939705405],
  [0.02879842920831339],
  [0.02890958947892114],
  [0.02

If the training is adequate x ≈ 1 ∀ x in the following:

In [34]:
t = {target: [
        outputs for outputs in test_outputs[target]['true']
] for target in targets}
t

{'above-ear': [[0.02102609246932776],
  [0.013553497342005377],
  [0.01592754662296081],
  [0.022141405611365024],
  [0.01635009548668533],
  [0.01395809170485838],
  [0.013167524333934413],
  [0.0170806351725729],
  [0.016840740780453948],
  [0.015915598248519278],
  [0.029028047796949556],
  [0.02264117865311729],
  [0.01743616511081432],
  [0.012425154498140425],
  [0.01936034112232813],
  [0.023392517098408658],
  [0.022513150599987476],
  [0.020286787089150514],
  [0.006973506166081466],
  [0.025508706050593615],
  [0.020902555314321277],
  [0.017275203464352146],
  [0.001742470576575998],
  [0.026504518633954435],
  [0.025331909825950058],
  [0.02119242345774712],
  [0.007037073885239996],
  [0.025594819349746993],
  [0.017746157664095312],
  [0.020058650528130596],
  [0.009940413532912288],
  [9.038111932336034e-05],
  [0.00023280938210900766],
  [0.0016601558174967161],
  [0.016639450367323096],
  [0.018056827333616268],
  [0.0014190333406002321],
  [0.009585482350080627],
  [0

Finally, if training is adequate, f ≪ t:

In [42]:
f_mean = {
    target: np.mean(f[target]) for target in targets if target in f and len(f[target])
}
t_mean = {
    target: np.mean(t[target]) for target in targets if target in t and len(t[target])
}
for target in t_mean:
    print(target)
    print(
        "f = {0}\nt = {1}\n{0} ≪ {1} ?\n".format(
            str(f_mean[target]),
            str(t_mean[target])
        ) if f_mean[target] < t_mean[target] else "f = {0}\nt = {1}\n{2}".format(
            str(f_mean[target]),
            str(t_mean[target]),
            stylize(
                "Nope. f > t\n",
                colored.fg("red")
            )
        )
    )

eyebrow
f = 0.008489704534989123
t = 0.02561092061950841
0.008489704534989123 ≪ 0.02561092061950841 ?

nose
f = 0.03515781801575057
t = 0.016283623121577818
Nope. f > t

above-ear
f = 0.00653904759273619
t = 0.01961381476531354
0.00653904759273619 ≪ 0.01961381476531354 ?

behind-ear
f = 0.027924609290320774
t = 0.06572574269151224
0.027924609290320774 ≪ 0.06572574269151224 ?

chin
f = 0.018913554833885723
t = 0.0629038943357809
0.018913554833885723 ≪ 0.0629038943357809 ?

cheek
f = 0.03890080339336535
t = 0.0999567086908781
0.03890080339336535 ≪ 0.0999567086908781 ?

forehead
f = 0.048523034617559586
t = 0.066982449524999
0.048523034617559586 ≪ 0.066982449524999 ?

top-head
f = 0.028320854995797323
t = 0.07034209948225449
0.028320854995797323 ≪ 0.07034209948225449 ?

back-head
f = 0.03394205684983784
t = 0.0928826121840425
0.03394205684983784 ≪ 0.0928826121840425 ?

opposite-face
f = 0.013262460684087114
t = 0.13447360968991673
0.013262460684087114 ≪ 0.13447360968991673 ?



---
### Try with demo data

In [43]:
with open(
    'data/demo_data.json',
    'r'
) as fp:
    demo_data = json.load(
        fp
    )[0]

In [44]:
scale = list(
    pd.DataFrame(
        [
            a[0:5] for a in [
                *demo_data["true"],
                *demo_data["false"]
            ]
        ]
    ).astype('float').max(axis=0)
)
demo_test = {
    "train":[
        *[{
            "input": [
                float(d)/scale[datum_i] for datum_i, d in enumerate(datum[0:5])
            ],
            "output": [1]
        } for datum in demo_data["true"][0:40]],
        *[{
            "input": [
                float(d)/scale[datum_i] for datum_i, d in enumerate(datum[0:5])
            ],
            "output": [0]
        } for datum in demo_data["false"][0:40]]
    ],
    "test_true": [[
                float(d)/scale[datum_i] for datum_i, d in enumerate(datum[0:5])
            ] for datum in demo_data["true"][41:]],
    "test_false": [[
                float(d)/scale[datum_i] for datum_i, d in enumerate(datum[0:5])
            ] for datum in demo_data["false"][41:]]
}

In [45]:
%%node
var LSTM5 = lstm.train_lstm([5,5,2,1], demo_test["train"], 0.06, 0.06, 3000);

TRAINING 🏋 interations:3000 🏋 minimum error:0.06 🏋 rate:0.06
iterations 5 error 0.7176128541888434 rate 0.06
iterations 10 error 0.6982012337977093 rate 0.06
iterations 15 error 0.6995249375563095 rate 0.06
iterations 20 error 0.7141898165156951 rate 0.06
iterations 25 error 0.6960532606961647 rate 0.06
iterations 30 error 0.6963383983849549 rate 0.06
iterations 35 error 0.6850008782401906 rate 0.06
iterations 40 error 0.6869078844078922 rate 0.06
iterations 45 error 0.6762224066302895 rate 0.06
iterations 50 error 0.683080201668908 rate 0.06
iterations 55 error 0.6750890815014035 rate 0.06
iterations 60 error 0.6514714847116037 rate 0.06
iterations 65 error 0.6524198896480392 rate 0.06
iterations 70 error 0.6609594394153746 rate 0.06
iterations 75 error 0.6463336047473002 rate 0.06
iterations 80 error 0.6430200121025785 rate 0.06
iterations 85 error 0.6519285556573546 rate 0.06
iterations 90 error 0.643228766862508 rate 0.06
iterations 95 error 0.6343045939692862 rate 0.06
iterations 

In [47]:
%%node
var demo_test_outputs = {"true":[],"false":[]}
for(var iteration=0; iteration < demo_test["test_true"].length; iteration++){
    var op = LSTM5.activate(demo_test["test_true"][iteration]);
    demo_test_outputs["true"].push(op);
}
for(var iteration=0; iteration < demo_test["test_false"].length; iteration++){
    demo_test_outputs["false"].push(LSTM5.activate(demo_test["test_false"][iteration]));
}

... ... ...
... ...


In [48]:
demo_test_outputs

{'false': [[0.9369284419405952],
  [0.9718886796832733],
  [0.8604860261178248],
  [0.5561251992379272],
  [0.016624282208243704],
  [0.00039240757018500636],
  [2.0184519711395964e-05],
  [9.717991816267999e-06],
  [3.2620037903688403e-06]],
 'true': [[0.9250166953343892],
  [0.9274044493231222],
  [0.996783304361895],
  [0.9968793152438503],
  [0.9969938749551247],
  [0.9821942859921602],
  [0.9863869855548448],
  [0.9757638908681954],
  [0.996742625262968]]}

In [49]:
np.mean(demo_test_outputs['false'])

0.3713864668081519

In [50]:
np.mean(demo_test_outputs['true'])

0.9760183807662833